# AutoTrain

## Imports

In [1]:
import os
import subprocess

import yaml

## Config

In [3]:
from huggingface_hub import login, get_token
login()

### Template
Im creating a template so we can iterate through each of our experiments.

Here you can see a few design decisions:
- We leave `project_name` and `text_column` empty to overwrite later per experiment
- We log in tensorboard, you can use wandb, but you will need to install it in the AutoTrain env that is run on spaces, which gets complex
- I choose an `l4x1` from [these options](https://github.com/huggingface/autotrain-advanced/blob/2d787b2033414d06f1e9be2ea0caacad3097f5e8/src/autotrain/backends/base.py#L21)
    - This is a [well priced](https://huggingface.co/pricing#spaces) way of training a 7B moodel 
    - It's very efficient as well at 24GB VRAM
- It's becoming less common to use a `valid_split` 
- I run 2 epochs as the loss still decreases steadily, but some say for LoRAs you should just do 1
- Its a good idea use `all-linear` when using LoRA 

In [4]:
# Base config
config_template = {
    "task": "llm-sft",
    "base_model": "mistralai/Mistral-7B-Instruct-v0.3",
    "project_name": "",
    "log": "tensorboard",
    "backend": "spaces-l4x1",
    "data": {
        "path": "derek-thomas/labeled-multiple-choice-explained-mistral-tokenized",
        "train_split": "train",
        "valid_split": None,
        "chat_template": "none",
        "column_mapping": {
            "text_column": ""
            },
        },
    "params": {
        "block_size": 512,
        "model_max_length": 1500,
        "epochs": 2,
        "batch_size": 1,
        "lr": 3e-5,
        "peft": True,
        "quantization": "int4",
        "target_modules": "all-linear",
        "padding": "right",
        "optimizer": "adamw_torch",
        "scheduler": "linear",
        "gradient_accumulation": 8,
        "mixed_precision": "bf16",
        },
    "hub": {
        "username": "derek-thomas",
        "token": get_token(),
        "push_to_hub": True,
        },
}

### Experiments
Here we choose the `project_name` and `text_column` for each experiment.

In [5]:
project_suffixes = ["RFA-gpt3-5", "RFA-mistral", "FAR-gpt3-5", "FAR-mistral", "FA"]
text_columns = ["conversation_RFA_gpt3_5", "conversation_RFA_mistral", "conversation_FAR_gpt3_5",
                "conversation_FAR_mistral", "conversation_FA"]

Directory to store generated configs

In [6]:
output_dir = "./autotrain_configs"
os.makedirs(output_dir, exist_ok=True)

## AutoTrain for each Experiment

In [9]:
# Generate configs and run commands
for project_suffix, text_column in zip(project_suffixes, text_columns):
    # Modify the config
    config = config_template.copy()
    config["project_name"] = f"mistral-v03-poe-{project_suffix}"
    config["data"]["column_mapping"]["text_column"] = text_column

    # Save the config to a YAML file
    config_path = os.path.join(output_dir, f"{text_column}.yml")
    with open(config_path, "w") as f:
        yaml.dump(config, f)

    # Run the command
    print(f"Running autotrain with config: {config_path}")
    subprocess.run(["autotrain", "--config", config_path])

Running autotrain with config: ./autotrain_configs/conversation_RFA_gpt3_5.yml
INFO     | 2024-12-12 20:45:45 | autotrain.cli.autotrain:main:60 - Using AutoTrain configuration: ./autotrain_configs/conversation_RFA_gpt3_5.yml
INFO     | 2024-12-12 20:45:45 | autotrain.parser:__post_init__:170 - Running task: lm_training
INFO     | 2024-12-12 20:45:45 | autotrain.parser:__post_init__:171 - Using backend: spaces-l4x1
INFO     | 2024-12-12 20:45:45 | autotrain.parser:run:234 - {'model': 'mistralai/Mistral-7B-Instruct-v0.3', 'project_name': 'mistral-v03-poe-RFA-gpt3-5', 'data_path': 'derek-thomas/labeled-multiple-choice-explained-mistral-tokenized', 'train_split': 'train', 'valid_split': None, 'add_eos_token': True, 'block_size': 512, 'model_max_length': 1500, 'padding': 'right', 'trainer': 'sft', 'use_flash_attention_2': False, 'log': 'tensorboard', 'disable_gradient_checkpointing': False, 'logging_steps': -1, 'eval_strategy': 'epoch', 'save_total_limit': 1, 'auto_find_batch_size': False, 